In [1]:
%env PATH=/appl/gams/47.6.0:$PATH
%env LD_LIBRARY_PATH=/appl/gams/47.6.0:$LD_LIBRARY_PATH

env: PATH=/appl/gams/47.6.0:$PATH
env: LD_LIBRARY_PATH=/appl/gams/47.6.0:$LD_LIBRARY_PATH


In [2]:

import Functions_analysis as FA
import os

YEAR = '2050'

Nordics = ['DENMARK', 'NORWAY', 'SWEDEN', 'FINLAND']
EU_North = ['DENMARK', 'NORWAY', 'SWEDEN', 'FINLAND', 'ESTONIA', 'LATVIA', 'LITHUANIA']
EU_West = ['FRANCE', 'GERMANY', 'NETHERLANDS', 'UNITED-KINGDOM', 'BELGIUM', 'LUXEMBOURG', 'AUSTRIA', 'SWITZERLAND', 'IRELAND']
EU_East = ['POLAND', 'CZECH_REPUBLIC', 'SLOVAKIA', 'ROMANIA', 'BULGARIA', 'HUNGARY']
EU_South = ['ITALY', 'SPAIN', 'PORTUGAL', 'SLOVENIA', 'CROATIA', 'ALBANIA', 'MALTA', 'CYPRUS', 'BOSNIA_AND_HERZEGOVINA', 'MONTENEGRO', 'NORTH_MACEDONIA', 'SERBIA', 'GREECE']

Input_data_path = f"../DATA/Input_data_{YEAR}.gdx"
MainResults_path = f"../DATA/MainResults_{YEAR}.gdx"
MonteCarlo_path = f"../DATA/MonteCarlo_EU_{YEAR}.gdx"

In [ ]:
def Main_Analysis(MainResults_path, MonteCarlo_path, YEAR, Countries_from) :
    # Import results of the Main Result file
    df_PRO_BASE, df_CAP_BASE, df_XH2_CAP_BASE, df_XH2_FLOW_BASE = FA.Import_MainResults(MainResults_path)
    
    # Export all hydrogen results
    df_H2_CAP_BASE, df_H2_CAP_GREEN_BASE, df_H2_CAP_GREEN_tot_BASE, df_H2_CAP_BLUE_BASE, df_H2_CAP_BLUE_tot_BASE, df_H2_CAP_STO_BASE, df_H2_CAP_STO_tot_BASE = FA.H2_CAP(df_CAP_BASE, Countries_from, YEAR)
    df_H2_PRO_BASE, df_H2_PRO_GREEN_BASE, df_H2_PRO_GREEN_tot_BASE, df_H2_PRO_BLUE_BASE, df_H2_PRO_BLUE_tot_BASE, df_H2_PRO_STO_BASE, df_H2_PRO_STO_tot_BASE = FA.H2_PRO(df_PRO_BASE, df_CAP_BASE, Countries_from, YEAR)
    dict_df_XH2_CAP_TO_BASE = FA.XH2(df_XH2_CAP_BASE, Countries_from, YEAR)
    dict_df_XH2_FLOW_TO_BASE = FA.XH2(df_XH2_FLOW_BASE, Countries_from, YEAR)
        
    # Import resuls of the MonteCarlo file
    df_PRO_scen, df_CAP_scen, df_XH2_CAP_scen, df_XH2_FLOW_scen, scen = FA.Import_MonteCarlo(MonteCarlo_path)
    
    # Export all hydrogen results
    df_H2_CAP_scen, df_H2_CAP_GREEN_scen, df_H2_CAP_BLUE_scen, df_H2_CAP_STO_scen = FA.H2_CAP_scen(df_CAP_scen, scen, Countries_from, YEAR)
    df_H2_PRO_scen, df_H2_PRO_GREEN_scen, df_H2_PRO_BLUE_scen, df_H2_PRO_STO_scen = FA.H2_PRO_scen(df_PRO_scen, df_CAP_scen, scen, Countries_from, YEAR)
    df_XH2_CAP_tot_scen, dict_df_XH2_CAP_TO_scen = FA.XH2_scen(df_XH2_CAP_scen, scen, Countries_from, YEAR)
    df_XH2_FLOW_tot_scen, dict_df_XH2_FLOW_TO_scen = FA.XH2_scen(df_XH2_FLOW_scen, scen, Countries_from, YEAR)
    
    ECDF_Hist_PRO = FA.ECDF_Hist_PRO(df_H2_PRO_GREEN_scen, df_H2_PRO_BLUE_scen, df_H2_PRO_STO_scen, df_H2_PRO_GREEN_tot_BASE, df_H2_PRO_BLUE_tot_BASE, df_H2_PRO_STO_tot_BASE, Countries_from, YEAR)
    ECDF_Hist_CAP = FA.ECDF_Hist_CAP(df_H2_CAP_GREEN_scen, df_H2_CAP_BLUE_scen, df_H2_CAP_GREEN_tot_BASE, df_H2_CAP_BLUE_tot_BASE, Countries_from, YEAR)
    Violin_PRO = FA.Violin_PRO(df_H2_PRO_GREEN_scen, df_H2_PRO_BLUE_scen, df_H2_PRO_STO_scen, df_H2_PRO_GREEN_tot_BASE, df_H2_PRO_BLUE_tot_BASE, df_H2_PRO_STO_tot_BASE, Countries_from, YEAR)
    Violin_CAP = FA.Violin_CAP(df_H2_CAP_GREEN_scen, df_H2_CAP_BLUE_scen, df_H2_CAP_STO_scen, df_H2_CAP_GREEN_tot_BASE, df_H2_CAP_BLUE_tot_BASE, df_H2_CAP_STO_tot_BASE, Countries_from, YEAR)
    BoxPlot_CAP = FA.BoxPlot_Transmission(dict_df_XH2_CAP_TO_BASE, dict_df_XH2_CAP_TO_scen, Countries_from, YEAR, "Capacity")
    BoxPlot_FLOW = FA.BoxPlot_Transmission(dict_df_XH2_FLOW_TO_BASE, dict_df_XH2_FLOW_TO_scen, Countries_from, YEAR, "Flow")

In [4]:
def CCS_Analysis(MainResults_path, YEAR) :
    # Import results of the Main Result file
    result = FA.Import_CCS(MainResults_path,YEAR)
    print(f"The total captured CO2 for {YEAR} is {result} kton")
    return result

In [5]:
def RE_Limits_Analysis(Input_data_path, MonteCarlo_path, Countries, YEAR) :
    df_SUBTECH = FA.Import_Data(Input_data_path)
    df_RE_SUBTECH = FA.LIM_RE_CAP_scen(df_SUBTECH)
    df_PRO, df_CAP, df_XH2_CAP, df_XH2_FLOW, scen = FA.Import_MonteCarlo(MonteCarlo_path)
    df_RE_CAP = FA.RE_CAP_scen(df_CAP, YEAR)
    
    FA.COMP_RE_LIM(df_RE_SUBTECH, df_RE_CAP, Countries, YEAR)
    

In [6]:
CCS_Analysis(MainResults_path, YEAR)

The total captured CO2 for 2050 is 235585 kton


/work3/s233235/gams/lib/python3.12/site-packages/gams/transfer/containers/_container.py:73: UserWarning: The GAMS version (47.6.0) differs from the API version (48.1.0).
  ws = GamsWorkspace()
/work3/s233235/gams/lib/python3.12/site-packages/gams/core/numpy/gams2numpy.py:45: UserWarning: The GAMS version (47.6.0) differs from the API version (48.1.0).
  ws = GamsWorkspace(system_directory=system_directory)


235585

In [14]:
RE_Limits_Analysis(Input_data_path, MonteCarlo_path, ['DENMARK'], YEAR)

/work3/s233235/gams/lib/python3.12/site-packages/gams/transfer/containers/_container.py:73: UserWarning:

The GAMS version (47.6.0) differs from the API version (48.1.0).

/work3/s233235/gams/lib/python3.12/site-packages/gams/core/numpy/gams2numpy.py:45: UserWarning:

The GAMS version (47.6.0) differs from the API version (48.1.0).

/work3/s233235/GSA_Analysis/Monte_Carlo_Simulation/Functions_analysis.py:56: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.

/work3/s233235/gams/lib/python3.12/site-packages/gams/transfer/containers/_container.py:73: UserWarning:

The GAMS version (47.6.0) differs from the API version (48.1.0).

/work3/s233235/gams/lib/python3.12/site-packages/gams/core/numpy/gams2numpy.py:45: UserWarning:

The GAMS version (47.6.0) differs from the API version (48.1.0).

/work3/s233235/

In [8]:
Main_Analysis(MainResults_path, MonteCarlo_path, YEAR, EU_North)

/work3/s233235/gams/lib/python3.12/site-packages/gams/transfer/containers/_container.py:73: UserWarning:

The GAMS version (47.6.0) differs from the API version (48.1.0).

/work3/s233235/gams/lib/python3.12/site-packages/gams/core/numpy/gams2numpy.py:45: UserWarning:

The GAMS version (47.6.0) differs from the API version (48.1.0).

/work3/s233235/GSA_Analysis/Monte_Carlo_Simulation/Functions_analysis.py:130: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/work3/s233235/gams/lib/python3.12/site-packages/gams/transfer/containers/_container.py:73: UserWarning:

The GAMS version (47.6.0) differs from the API version (48.1.0).

/work3/s233235/gams/lib/python3.12/site-packages/gams/core/numpy/gams2numpy.py:45: UserWarning:

The GAMS version (47.6.0) di

/work3/s233235/GSA_Analysis/Monte_Carlo_Simulation/Functions_analysis.py:246: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [9]:
Main_Analysis(MainResults_path, MonteCarlo_path, YEAR, EU_South)

/work3/s233235/gams/lib/python3.12/site-packages/gams/transfer/containers/_container.py:73: UserWarning:

The GAMS version (47.6.0) differs from the API version (48.1.0).

/work3/s233235/gams/lib/python3.12/site-packages/gams/core/numpy/gams2numpy.py:45: UserWarning:

The GAMS version (47.6.0) differs from the API version (48.1.0).

/work3/s233235/GSA_Analysis/Monte_Carlo_Simulation/Functions_analysis.py:130: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/work3/s233235/gams/lib/python3.12/site-packages/gams/transfer/containers/_container.py:73: UserWarning:

The GAMS version (47.6.0) differs from the API version (48.1.0).

/work3/s233235/gams/lib/python3.12/site-packages/gams/core/numpy/gams2numpy.py:45: UserWarning:

The GAMS version (47.6.0) di

In [10]:
Main_Analysis(MainResults_path, MonteCarlo_path, YEAR, EU_West)

/work3/s233235/gams/lib/python3.12/site-packages/gams/transfer/containers/_container.py:73: UserWarning:

The GAMS version (47.6.0) differs from the API version (48.1.0).

/work3/s233235/gams/lib/python3.12/site-packages/gams/core/numpy/gams2numpy.py:45: UserWarning:

The GAMS version (47.6.0) differs from the API version (48.1.0).

/work3/s233235/GSA_Analysis/Monte_Carlo_Simulation/Functions_analysis.py:130: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/work3/s233235/gams/lib/python3.12/site-packages/gams/transfer/containers/_container.py:73: UserWarning:

The GAMS version (47.6.0) differs from the API version (48.1.0).

/work3/s233235/gams/lib/python3.12/site-packages/gams/core/numpy/gams2numpy.py:45: UserWarning:

The GAMS version (47.6.0) di

In [11]:
Main_Analysis(MainResults_path, MonteCarlo_path, YEAR, EU_East)

/work3/s233235/gams/lib/python3.12/site-packages/gams/transfer/containers/_container.py:73: UserWarning:

The GAMS version (47.6.0) differs from the API version (48.1.0).

/work3/s233235/gams/lib/python3.12/site-packages/gams/core/numpy/gams2numpy.py:45: UserWarning:

The GAMS version (47.6.0) differs from the API version (48.1.0).

/work3/s233235/GSA_Analysis/Monte_Carlo_Simulation/Functions_analysis.py:130: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/work3/s233235/gams/lib/python3.12/site-packages/gams/transfer/containers/_container.py:73: UserWarning:

The GAMS version (47.6.0) differs from the API version (48.1.0).

/work3/s233235/gams/lib/python3.12/site-packages/gams/core/numpy/gams2numpy.py:45: UserWarning:

The GAMS version (47.6.0) di